# 1. Imports

In [42]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from pandas import DataFrame, Series
import seaborn as sns
from tqdm.notebook import tqdm
from typing import Optional

import category_encoders
from category_encoders import WOEEncoder
from optuna import Trial
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score, make_scorer
from sklearn.model_selection import cross_val_score, KFold, StratifiedKFold
from sklearn.preprocessing import RobustScaler
from sklearn.pipeline import Pipeline

from lightgbm import LGBMClassifier
from xgboost import XGBClassifier
from catboost import CatBoostClassifier

from utils.eda import summary

# 2. Notebook settings

In [2]:
import warnings
warnings.filterwarnings("ignore")
pd.options.display.float_format = '{:,.2f}'.format

# 3. Data Load

In [3]:
test_df = pd.read_csv('test.csv')
train_df = pd.read_csv('train.csv')
submission_df = pd.read_csv('sample_submission.csv')

# 4. Data Cleaning 

In [4]:
cat_cols = [column for column in train_df.columns if train_df[column].dtype == 'object']
num_cols = train_df.select_dtypes(include=[np.number]).columns.tolist()

num_cols.remove('id')
num_cols.remove('CustomerId')
num_cols.remove('IsActiveMember')
num_cols.remove('HasCrCard')
num_cols.remove('Exited')
cat_cols.remove('Surname')
cat_cols.append('IsActiveMember')
cat_cols.append('HasCrCard')

train_df['HasCrCard'] = train_df['HasCrCard'].astype(bool)
train_df['IsActiveMember'] = train_df['IsActiveMember'].astype(bool)
test_df['HasCrCard'] = test_df['HasCrCard'].astype(bool)
test_df['IsActiveMember'] = test_df['IsActiveMember'].astype(bool)
train_df.head()

id  CustomerId         Surname  CreditScore Geography Gender   Age  Tenure  \
0   0    15674932  Okwudilichukwu          668    France   Male 33.00       3   
1   1    15749177   Okwudiliolisa          627    France   Male 33.00       1   
2   2    15694510           Hsueh          678    France   Male 40.00      10   
3   3    15741417             Kao          581    France   Male 34.00       2   
4   4    15766172       Chiemenam          716     Spain   Male 33.00       5   

     Balance  NumOfProducts  HasCrCard  IsActiveMember  EstimatedSalary  \
0       0.00              2       True           False       181,449.97   
1       0.00              2       True            True        49,503.50   
2       0.00              2       True           False       184,866.69   
3 148,882.54              1       True            True        84,560.88   
4       0.00              2       True            True        15,068.83   

   Exited  
0       0  
1       0  
2       0  
3       0  
4       0

# 5. Model Setup

In [55]:
class LogTransformer(BaseEstimator, TransformerMixin):
    def __init__(self, columns):
        self.columns = columns

    def fit(self, X, y=None):
        return self

    def transform(self, X):
        X = X.copy()
        for column in self.columns:
            X[column] = np.log1p(X[column])
        return X

In [56]:
def instantiate_woe_encoder(trial : Trial) -> WOEEncoder:
  params = {
    'sigma': trial.suggest_float('sigma', 0.001, 5),
    'regularization': trial.suggest_float('regularization', 0, 5),
    'randomized': trial.suggest_categorical('randomized', [True, False])
  }
  return WOEEncoder(**params)

def instantiate_robust_scaler(trial : Trial) -> RobustScaler:
  params = {
    'with_centering': trial.suggest_categorical(
      'with_centering', [True, False]
    ),
    'with_scaling': trial.suggest_categorical(
      'with_scaling', [True, False]
    )
  }
  return RobustScaler(**params)

def instantiate_catboost(trial : Trial) -> CatBoostClassifier:
  params = {
        "iterations": 500,
        "learning_rate": trial.suggest_float("learning_rate", 1e-3, 0.1, log=True),
        "depth": trial.suggest_int("depth", 1, 10),
        "subsample": trial.suggest_float("subsample", 0.05, 1.0),
        "colsample_bylevel": trial.suggest_float("colsample_bylevel", 0.05, 1.0),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 1, 100),
    }
  return CatBoostClassifier(**params)

def instantiate_logistic(trial : Trial) -> LogisticRegression:
  params = {
        'tol' : trial.suggest_uniform('tol' , 1e-6 , 1e-3),
        'C' : trial.suggest_loguniform("C", 1e-2, 1),
  }
  return LogisticRegression(**params)

def instantiate_xgboost(trial : Trial) -> XGBClassifier:
  params = {
        "learning_rate": trial.suggest_float("learning_rate", 1e-3, 0.1, log=True),
        "max_depth": trial.suggest_int("max_depth", 2, 10),
        "subsample": trial.suggest_float("subsample", 0.05, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.05, 1.0),
        "min_child_weight": trial.suggest_int("min_child_weight", 1, 20),
  }
  return XGBClassifier(**params)

def instantiate_lgbm(trial : Trial) -> LGBMClassifier:
  params = {
        "learning_rate": trial.suggest_float("learning_rate", 1e-3, 0.1, log=True),
        "max_depth": trial.suggest_int("max_depth", 2, 10),
        "subsample": trial.suggest_float("subsample", 0.05, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.05, 1.0),
        "min_child_weight": trial.suggest_int("min_child_weight", 1, 20),
  }
  return LGBMClassifier(**params)

def instantiate_numerical_pipeline(trial : Trial, log_columns: list[int]) -> Pipeline:
  pipeline = Pipeline([
    ('scaler', instantiate_robust_scaler(trial)),
    ('log_transformer', LogTransformer(columns=log_columns))
  ])
  return pipeline

def instantiate_categorical_pipeline(trial : Trial) -> Pipeline:
  pipeline = Pipeline([
    ('encoder', instantiate_woe_encoder(trial))
  ])
  return pipeline

In [57]:
from sklearn.compose import ColumnTransformer

def instantiate_processor(trial : Trial, numerical_columns : list[str], categorical_columns : list[str], log_columns : list[int]) -> ColumnTransformer:
  
  numerical_pipeline = instantiate_numerical_pipeline(trial, log_columns)
  categorical_pipeline = instantiate_categorical_pipeline(trial)
  
  processor = ColumnTransformer([
    ('numerical_pipeline', numerical_pipeline, numerical_columns),
    ('categorical_pipeline', categorical_pipeline, categorical_columns)
  ])
  
  return processor

def instantiate_model(trial : Trial, numerical_columns : list[str], categorical_columns : list[str], algo: str, log_columns : list[int]) -> Pipeline:
  
  processor = instantiate_processor(
    trial, numerical_columns, categorical_columns, log_columns
  )
  
  if algo == 'cat':
    model = instantiate_catboost(trial)
  elif algo == 'log':
    model = instantiate_logistic(trial)
  elif algo == 'xgb':
    model = instantiate_xgboost(trial)
  elif algo == 'lgbm':
    model = instantiate_lgbm(trial)
  
  model = Pipeline([
    ('processor', processor),
    ('extra_trees', model)
  ])
  
  return model

In [59]:
def objective(trial : Trial, X : DataFrame, y : np.ndarray | Series, algo: str, log_columns : list[int], 
              numerical_columns : Optional[list[str]]=None, categorical_columns : Optional[list[str]]=None, 
              random_state : int=42) -> float:
  if numerical_columns is None:
    numerical_columns = [
      *X.select_dtypes(exclude=['object', 'category']).columns
    ]
  
  if categorical_columns is None:
    categorical_columns = [
      *X.select_dtypes(include=['object', 'category']).columns
    ]
  
  model = instantiate_model(trial, numerical_columns, categorical_columns, algo, log_columns)
  
  skf = StratifiedKFold(n_splits=10, shuffle=True, random_state=random_state)
  roc_auc_scorer = make_scorer(roc_auc_score, needs_proba=True)
  scores = cross_val_score(model, X, y, scoring=roc_auc_scorer, cv=skf)
  
  return np.min([np.mean(scores), np.median([scores])])

# 6. Training

In [60]:
from optuna import create_study

study = create_study(study_name='optimization', direction='maximize')

study.optimize(lambda trial: objective(trial, train_df[cat_cols + num_cols], train_df['Exited'], algo='cat', log_columns=[1]), n_trials=100)

[I 2024-01-13 19:12:59,834] A new study created in memory with name: optimization


Learning rate set to 0.381289
0:	learn: 0.4448310	total: 14.8ms	remaining: 2.95s
1:	learn: 0.3772705	total: 23.4ms	remaining: 2.32s
2:	learn: 0.3473358	total: 32.5ms	remaining: 2.13s
3:	learn: 0.3355133	total: 42.4ms	remaining: 2.08s
4:	learn: 0.3310465	total: 50.6ms	remaining: 1.97s
5:	learn: 0.3279155	total: 58.5ms	remaining: 1.89s
6:	learn: 0.3257996	total: 65.6ms	remaining: 1.81s
7:	learn: 0.3241284	total: 73ms	remaining: 1.75s
8:	learn: 0.3237279	total: 79.7ms	remaining: 1.69s
9:	learn: 0.3229670	total: 87ms	remaining: 1.65s
10:	learn: 0.3222227	total: 96.3ms	remaining: 1.65s
11:	learn: 0.3217809	total: 104ms	remaining: 1.63s
12:	learn: 0.3213554	total: 112ms	remaining: 1.61s
13:	learn: 0.3210166	total: 119ms	remaining: 1.58s
14:	learn: 0.3208222	total: 126ms	remaining: 1.56s
15:	learn: 0.3205801	total: 134ms	remaining: 1.54s
16:	learn: 0.3203884	total: 143ms	remaining: 1.53s
17:	learn: 0.3201562	total: 150ms	remaining: 1.52s
18:	learn: 0.3199887	total: 160ms	remaining: 1.52s
19:	

[I 2024-01-13 19:13:20,560] Trial 0 finished with value: 0.8874703385618812 and parameters: {'with_centering': True, 'with_scaling': True, 'sigma': 1.4930413548896613, 'regularization': 1.9931399965642704, 'randomized': False, 'n_estimators': 200, 'max_depth': 5}. Best is trial 0 with value: 0.8874703385618812.


181:	learn: 0.3048160	total: 1.42s	remaining: 140ms
182:	learn: 0.3047490	total: 1.43s	remaining: 133ms
183:	learn: 0.3046792	total: 1.43s	remaining: 125ms
184:	learn: 0.3046198	total: 1.44s	remaining: 117ms
185:	learn: 0.3045750	total: 1.45s	remaining: 109ms
186:	learn: 0.3045118	total: 1.46s	remaining: 101ms
187:	learn: 0.3044602	total: 1.47s	remaining: 93.5ms
188:	learn: 0.3043831	total: 1.47s	remaining: 85.7ms
189:	learn: 0.3043289	total: 1.48s	remaining: 77.9ms
190:	learn: 0.3042782	total: 1.49s	remaining: 70.1ms
191:	learn: 0.3042048	total: 1.5s	remaining: 62.3ms
192:	learn: 0.3041474	total: 1.5s	remaining: 54.5ms
193:	learn: 0.3040602	total: 1.51s	remaining: 46.7ms
194:	learn: 0.3039985	total: 1.52s	remaining: 38.9ms
195:	learn: 0.3039547	total: 1.53s	remaining: 31.1ms
196:	learn: 0.3039037	total: 1.53s	remaining: 23.4ms
197:	learn: 0.3038487	total: 1.54s	remaining: 15.6ms
198:	learn: 0.3037852	total: 1.55s	remaining: 7.8ms
199:	learn: 0.3037031	total: 1.56s	remaining: 0us
Learn

[I 2024-01-13 19:13:26,052] Trial 1 finished with value: 0.8845878646545353 and parameters: {'with_centering': False, 'with_scaling': False, 'sigma': 1.3686420488898923, 'regularization': 1.7015239338609707, 'randomized': True, 'n_estimators': 50, 'max_depth': 2}. Best is trial 0 with value: 0.8874703385618812.


...

72:	learn: 0.3200129	total: 196ms	remaining: 126ms
73:	learn: 0.3199788	total: 199ms	remaining: 124ms
74:	learn: 0.3199460	total: 202ms	remaining: 121ms
75:	learn: 0.3199256	total: 205ms	remaining: 118ms
76:	learn: 0.3198944	total: 207ms	remaining: 116ms
77:	learn: 0.3198665	total: 210ms	remaining: 113ms
78:	learn: 0.3198450	total: 213ms	remaining: 110ms
79:	learn: 0.3198045	total: 215ms	remaining: 108ms
80:	learn: 0.3197806	total: 218ms	remaining: 105ms
81:	learn: 0.3197488	total: 221ms	remaining: 102ms
82:	learn: 0.3197172	total: 224ms	remaining: 99.8ms
83:	learn: 0.3196646	total: 227ms	remaining: 97.2ms
84:	learn: 0.3196291	total: 230ms	remaining: 94.5ms
85:	learn: 0.3196166	total: 232ms	remaining: 91.8ms
86:	learn: 0.3195857	total: 235ms	remaining: 89.1ms
87:	learn: 0.3195660	total: 238ms	remaining: 86.5ms
88:	learn: 0.3195254	total: 241ms	remaining: 84ms
89:	learn: 0.3194874	total: 244ms	remaining: 81.4ms
90:	learn: 0.3194710	total: 247ms	remaining: 78.8ms
91:	learn: 0.3194537	tot

[I 2024-01-13 19:24:38,519] Trial 66 finished with value: 0.8875204466005268 and parameters: {'with_centering': True, 'with_scaling': False, 'sigma': 2.0273509769675315, 'regularization': 3.9459600246743096, 'randomized': False, 'n_estimators': 140, 'max_depth': 4}. Best is trial 43 with value: 0.8884633854180837.


112:	learn: 0.3130088	total: 397ms	remaining: 94.9ms
113:	learn: 0.3129714	total: 401ms	remaining: 91.4ms
114:	learn: 0.3129148	total: 404ms	remaining: 87.9ms
115:	learn: 0.3128625	total: 408ms	remaining: 84.4ms
116:	learn: 0.3128151	total: 412ms	remaining: 81ms
117:	learn: 0.3127603	total: 417ms	remaining: 77.7ms
118:	learn: 0.3127005	total: 423ms	remaining: 74.6ms
119:	learn: 0.3126738	total: 428ms	remaining: 71.3ms
120:	learn: 0.3126095	total: 435ms	remaining: 68.2ms
121:	learn: 0.3125402	total: 441ms	remaining: 65.1ms
122:	learn: 0.3124903	total: 452ms	remaining: 62.5ms
123:	learn: 0.3124686	total: 461ms	remaining: 59.5ms
124:	learn: 0.3123701	total: 468ms	remaining: 56.2ms
125:	learn: 0.3123391	total: 473ms	remaining: 52.5ms
126:	learn: 0.3122942	total: 477ms	remaining: 48.8ms
127:	learn: 0.3122452	total: 480ms	remaining: 45ms
128:	learn: 0.3121834	total: 484ms	remaining: 41.3ms
129:	learn: 0.3121226	total: 488ms	remaining: 37.5ms
130:	learn: 0.3120904	total: 491ms	remaining: 33.8

[I 2024-01-13 19:24:50,601] Trial 67 finished with value: 0.8867534650035735 and parameters: {'with_centering': True, 'with_scaling': False, 'sigma': 1.820730170013796, 'regularization': 4.243790769613182, 'randomized': False, 'n_estimators': 130, 'max_depth': 7}. Best is trial 43 with value: 0.8884633854180837.


116:	learn: 0.3013176	total: 601ms	remaining: 66.8ms
117:	learn: 0.3011469	total: 607ms	remaining: 61.7ms
118:	learn: 0.3009536	total: 616ms	remaining: 56.9ms
119:	learn: 0.3007757	total: 621ms	remaining: 51.8ms
120:	learn: 0.3006693	total: 628ms	remaining: 46.7ms
121:	learn: 0.3005664	total: 636ms	remaining: 41.7ms
122:	learn: 0.3004549	total: 642ms	remaining: 36.5ms
123:	learn: 0.3003546	total: 649ms	remaining: 31.4ms
124:	learn: 0.3002119	total: 656ms	remaining: 26.2ms
125:	learn: 0.3000738	total: 663ms	remaining: 21.1ms
126:	learn: 0.2999651	total: 670ms	remaining: 15.8ms
127:	learn: 0.2998103	total: 678ms	remaining: 10.6ms
128:	learn: 0.2996860	total: 684ms	remaining: 5.3ms
129:	learn: 0.2995524	total: 692ms	remaining: 0us
Learning rate set to 0.5
0:	learn: 0.4706901	total: 6ms	remaining: 714ms
1:	learn: 0.3943484	total: 12.5ms	remaining: 735ms
2:	learn: 0.3556363	total: 17.7ms	remaining: 692ms
3:	learn: 0.3381241	total: 23.4ms	remaining: 679ms
4:	learn: 0.3318880	total: 28.8ms	re

# 7. Model evaluation

In [19]:
study.best_params
best_trial = study.best_trial

In [21]:
model = instantiate_model(best_trial, num_cols, cat_cols, algo='cat')
model.fit(train_df[cat_cols + num_cols], train_df['Exited'])

Learning rate set to 0.489395
0:	learn: 0.4969153	total: 4.08ms	remaining: 648ms
1:	learn: 0.4235073	total: 7.08ms	remaining: 559ms
2:	learn: 0.3848073	total: 10.1ms	remaining: 527ms
3:	learn: 0.3645509	total: 12.8ms	remaining: 500ms
4:	learn: 0.3544694	total: 15.9ms	remaining: 492ms
5:	learn: 0.3412182	total: 18.8ms	remaining: 482ms
6:	learn: 0.3372156	total: 22.2ms	remaining: 485ms
7:	learn: 0.3340531	total: 25ms	remaining: 475ms
8:	learn: 0.3296247	total: 28.1ms	remaining: 472ms
9:	learn: 0.3282180	total: 30.8ms	remaining: 462ms
10:	learn: 0.3272080	total: 33.6ms	remaining: 455ms
11:	learn: 0.3264568	total: 36.4ms	remaining: 449ms
12:	learn: 0.3258838	total: 39.3ms	remaining: 445ms
13:	learn: 0.3248434	total: 42ms	remaining: 438ms
14:	learn: 0.3245347	total: 45ms	remaining: 435ms
15:	learn: 0.3242591	total: 47.6ms	remaining: 429ms
16:	learn: 0.3239048	total: 50.5ms	remaining: 425ms
17:	learn: 0.3236409	total: 53ms	remaining: 418ms
18:	learn: 0.3232960	total: 55.8ms	remaining: 414ms


Pipeline(steps=[('processor',
                 ColumnTransformer(transformers=[('numerical_pipeline',
                                                  Pipeline(steps=[('scaler',
                                                                   RobustScaler(with_centering=False,
                                                                                with_scaling=False))]),
                                                  ['CreditScore', 'Age',
                                                   'Tenure', 'Balance',
                                                   'NumOfProducts',
                                                   'EstimatedSalary']),
                                                 ('categorical_pipeline',
                                                  Pipeline(steps=[('encoder',
                                                                   WOEEncoder(regularization=4.050335147681011,
                                                                              sigma=2.7335999531957684))]),
                                                  ['Geography', 'Gender',
                                                   'IsActiveMember',
                                                   'HasCrCard'])])),
                ('extra_trees',
                 <catboost.core.CatBoostClassifier object at 0x161833710>)])

In [ ]:
# Check for underfitting/overfitting by analyzing splits
# folds = range(1, kf.get_n_splits() + 1)
# plt.plot(folds, rmse_train, 'o-', color='green', label='train')
# plt.plot(folds, rmse_test, 'o-', color='red', label='test')
# plt.legend()
# plt.grid()
# plt.xlabel('Number of fold')
# plt.ylabel('mean squared error')
# plt.show()

In [23]:
test_probabilities = model.predict_proba(test_df[cat_cols + num_cols])[:, 1]
test_preds = model.predict(test_df[cat_cols + num_cols])

In [24]:
test_df['predictions'] = test_preds
test_df.head()

cutoff = 0.95 # Probability CutOff...
pseudo_set_1 = test_df[test_df['predictions'] > cutoff]
pseudo_set_1['Exited'] = 1
pseudo_set_1.drop(columns=['predictions'], axis = 1, inplace=True)

pseudo_set_2 = test_df[test_df['predictions'] < 1 - cutoff]
pseudo_set_2['Exited'] = 0
pseudo_set_2.drop(columns=['predictions'], axis = 1, inplace=True)

pseudo_set = pd.concat([pseudo_set_1,pseudo_set_2])
pseudo_set.shape

(110023, 14)

In [25]:
pseudo_train_df = pd.concat([train_df, pseudo_set])
skf = StratifiedKFold(n_splits=10, shuffle=True, random_state=42)
roc_auc_scorer = make_scorer(roc_auc_score, needs_proba=True)
scores = cross_val_score(model, pseudo_train_df[cat_cols + num_cols], pseudo_train_df['Exited'], scoring=roc_auc_scorer, cv=skf)
np.min([np.mean(scores), np.median([scores])])

Learning rate set to 0.5
0:	learn: 0.4617753	total: 8.51ms	remaining: 1.35s
1:	learn: 0.3735567	total: 13ms	remaining: 1.02s
2:	learn: 0.3319598	total: 17.3ms	remaining: 908ms
3:	learn: 0.3077432	total: 21.2ms	remaining: 826ms
4:	learn: 0.2859915	total: 25.4ms	remaining: 786ms
5:	learn: 0.2754827	total: 29.7ms	remaining: 762ms
6:	learn: 0.2687603	total: 33.8ms	remaining: 738ms
7:	learn: 0.2646252	total: 37.4ms	remaining: 711ms
8:	learn: 0.2617420	total: 41ms	remaining: 687ms
9:	learn: 0.2597441	total: 45.2ms	remaining: 678ms
10:	learn: 0.2563982	total: 50ms	remaining: 677ms
11:	learn: 0.2543478	total: 53.9ms	remaining: 665ms
12:	learn: 0.2535050	total: 57.5ms	remaining: 650ms
13:	learn: 0.2523054	total: 61.5ms	remaining: 641ms
14:	learn: 0.2516388	total: 65.9ms	remaining: 637ms
15:	learn: 0.2510569	total: 69.7ms	remaining: 628ms
16:	learn: 0.2503919	total: 73.5ms	remaining: 618ms
17:	learn: 0.2500136	total: 77.4ms	remaining: 611ms
18:	learn: 0.2497377	total: 81.3ms	remaining: 603ms
19:

0.9248317176830619

In [37]:
model.fit(pseudo_train_df[cat_cols + num_cols], pseudo_train_df['Exited'])
test_probabilities = model.predict_proba(test_df[cat_cols + num_cols])[:,1]

Learning rate set to 0.5
0:	learn: 0.4616686	total: 6.72ms	remaining: 1.07s
1:	learn: 0.3735463	total: 11.4ms	remaining: 898ms
2:	learn: 0.3319151	total: 21.7ms	remaining: 1.14s
3:	learn: 0.3077329	total: 26.9ms	remaining: 1.05s
4:	learn: 0.2859686	total: 32ms	remaining: 992ms
5:	learn: 0.2754660	total: 37ms	remaining: 949ms
6:	learn: 0.2688911	total: 41.4ms	remaining: 906ms
7:	learn: 0.2639143	total: 45.7ms	remaining: 867ms
8:	learn: 0.2613493	total: 50.2ms	remaining: 842ms
9:	learn: 0.2592178	total: 54.6ms	remaining: 819ms
10:	learn: 0.2578713	total: 58.5ms	remaining: 793ms
11:	learn: 0.2542332	total: 62.8ms	remaining: 775ms
12:	learn: 0.2528705	total: 67.5ms	remaining: 763ms
13:	learn: 0.2519566	total: 72ms	remaining: 751ms
14:	learn: 0.2513697	total: 76.2ms	remaining: 736ms
15:	learn: 0.2505395	total: 80.4ms	remaining: 724ms
16:	learn: 0.2501198	total: 85ms	remaining: 715ms
17:	learn: 0.2497521	total: 89.1ms	remaining: 703ms
18:	learn: 0.2494902	total: 93.3ms	remaining: 693ms
19:	l

In [38]:
sub = pd.DataFrame()
sub['id'] = test_df['id']
sub['Exited'] = test_probabilities
sub = sub.set_index('id')
sub.head()

Exited
id            
165034    0.02
165035    0.91
165036    0.01
165037    0.13
165038    0.28

In [39]:
sub.to_csv('submission.csv')